In [1]:
from hicmatrix import HiCMatrix as hm
from hicmatrix.lib import MatrixFileHandler
import numpy as np
import pandas as pd
from scipy import stats, sparse
import bottleneck
from scipy.stats import mannwhitneyu
import h5py
import os.path
import gc
import os
import matplotlib.pyplot as plt
from pyranges import read_gtf


from umap import UMAP
#import plotly.express as px
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
import scipy.spatial as sp, scipy.cluster.hierarchy as hc

import seaborn as sns


import anndata as ad
import scanpy as sc


INFO:numexpr.utils:Note: NumExpr detected 32 cores but "NUMEXPR_MAX_THREADS" not set, so enforcing safe limit of 8.
INFO:numexpr.utils:NumExpr defaulting to 8 threads.


In [1]:
pwd

'/home/lohia'

In [2]:

def marker_list_gene_symbol(marker_list, species):
    if species == "human":
        marker_list['gene'] = marker_list['gene'].str.upper()
        df_ensg_name = pd.read_csv(f'{base_folder}/hi_c_data_processing/genomes_jlee/ensg_geneid_symbol.csv', sep='\t')[['Ensembl_gene_identifier', 'Symbol']]
        
    else:
        df_ensg_name = pd.read_csv(f'{base_folder}/hi_c_data_processing/genomes_jlee//mouse_geneid_symbol.txt', sep='\t', names=['Ensembl_gene_identifier', 'Symbol'])

    

    marker_list = marker_list.merge(df_ensg_name.drop_duplicates(), right_on='Symbol', left_on='gene') 
    
    return marker_list



def get_input_matrix(process_type, marker_list, df_regions_bed, gene_vector_file, outfile, gene_annot_file):
    
    
    cat_list_genes = marker_list['Ensembl_gene_identifier'].drop_duplicates().tolist()

    bins_bed = pd.read_csv(df_regions_bed, names=['chr', 'start', 'end'])
    bins_bed['bin_id'] = bins_bed.index.tolist()

    #bins_bed.to_csv(f'{input_path}/all_bins_true.bed', index=False, header=False, sep='\t')

    chr_list = bins_bed.drop_duplicates(subset=['chr'])['chr'].tolist()

    gtf = read_gtf(gene_annot_file)
    genes = gtf.df.loc[gtf.df['Feature'] == 'gene'].copy()
    genes['gene_id'] = [x.split('.')[0] for x in genes['gene_id']]
    genes['gene_id'].drop_duplicates(inplace=True)

    if not genes['Chromosome'].str.startswith('chr').any():
        genes['Chromosome'] = [f'chr{x}' for x in genes['Chromosome']]

    #df_genes_chrom = pd.read_csv(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/all_gene_max.bed', names=['chrom', 'st', 'end', 'gene'])
                
    
    with h5py.File(gene_vector_file, 'r') as hf:
            tot_g = (list(hf.keys()))
    
    
    marker_contacts_list_inter = []

    gene_list = []
        
    
    
    for each_chrom in chr_list:

            marker_contacts_inter = []

            #for key in all_background_markers:
            for key, m_chrom in zip(genes['gene_id'].tolist(), genes['Chromosome'].tolist()):
               if key in tot_g:
                 if key in cat_list_genes:
                   if m_chrom == each_chrom:
                         
     
                        with h5py.File(gene_vector_file, 'r') as hf:
                                                        gene_list.append(key)
                                                        my_data = hf[key][()]
                                                        marker_contacts_inter.append(my_data)
            marker_contacts_list_inter.append(np.array(marker_contacts_inter))

                                            
    if process_type == 'intra':
        my_data = sparse.block_diag(marker_contacts_list_inter).toarray()
    else:
        my_data = np.concatenate(marker_contacts_list_inter)


    adata = ad.AnnData(my_data)
    adata.obs_names = [i for i in gene_list]
    adata.var_names = [f"bin_{i}" for i in bins_bed['bin_id'].tolist()]

    adata.write(outfile, compression="gzip")
    
    return 












In [3]:
    #obtain marker list
    base_folder='/grid/gillis/data_norepl/lohia'
    marker_list_mouse_brain = pd.read_csv(f'{base_folder}/hi_c_data_processing/notebooks/metamarkers/mouse/joint_subclass_markers.csv.gz', skiprows=1)
    marker_list_mouse_brain_type = pd.read_csv(f'{base_folder}/hi_c_data_processing/notebooks/metamarkers/mouse/joint_cluster_markers.csv.gz', skiprows=1)
    marker_list_mouse_blood = marker_list = pd.read_csv(f'{base_folder}/blood_ben/media-2.csv')


    marker_list_human_brain = pd.read_csv(f'{base_folder}/hi_c_data_processing/notebooks/metamarkers/human/subclass_markers_top1000.csv.gz', skiprows=1)
    marker_list_human_brain_class = pd.read_csv(f'{base_folder}/hi_c_data_processing/notebooks/metamarkers/human/class_markers_top1000.csv.gz', skiprows=1)
    marker_list_human_brain_type = pd.read_csv(f'{base_folder}/hi_c_data_processing/notebooks/metamarkers/human/type_markers_top1000.csv.gz', skiprows=1)

    marker_list_list = []
    marker_list = pd.read_csv('/grid/gillis/data_norepl/lohia/heart_hamsini/Knight-Schrijver_celltype_markers_res2.csv.gz', skiprows=1)
    all_cell_types = marker_list.drop_duplicates(['cell_type'])['cell_type'].tolist()
    for group2 in all_cell_types:

                    m_tmp = marker_list[marker_list['cell_type']==group2]
                    m_tmp['recurrence'] = 1
                    m_tmp['n_datasets'] = 1

                    m_tmp['rank'] = [x+1 for x in range(m_tmp.shape[0])]
                    marker_list_list.append(m_tmp)
    marker_list = pd.concat(marker_list_list)
    marker_list_human_heart = marker_list



    #marker_list_input_dict[species] = marker_list_input_dict[species][marker_list_input_dict[species]['rank']<10]


/home/lohia/miniconda3/envs/hicexplorer/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (13,14,15,16,18) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,
/home/lohia/miniconda3/envs/hicexplorer/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (13,14,15,16,18,19) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,
/home/lohia/miniconda3/envs/hicexplorer/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (18,19,20,21) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,
/home/lohia/miniconda3/envs/hicexplorer/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (13,15,18,20,21)

In [24]:
for species in ['human', 'mouse']:
    for ice_type in ['none']:
    
        for resolution in ['40kbp_raw', '250kbp_raw', '100kbp_raw']:
            
            if ice_type == 'none':
                process_type_list = ['gw']
            else:
                process_type_list = ['intra', 'inter']
            for process_type in process_type_list:
            
                base_folder = '/grid/gillis/data_norepl/lohia/'
                SRP_name='aggregates'
                marker_list_input_dict = {}
                if species=='mouse':

                    marker_list_input_dict[species] = pd.concat([marker_list_gene_symbol(marker_list_mouse_brain, species), marker_list_gene_symbol(marker_list_mouse_brain_type, species), marker_list_gene_symbol(marker_list_mouse_blood, species)])

                if species=='human':

                    marker_list_input_dict[species] = pd.concat([marker_list_gene_symbol(marker_list_human_brain, species), marker_list_gene_symbol(marker_list_human_brain_type, species), marker_list_gene_symbol(marker_list_human_heart, species)])


                df_regions_bed = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/regions_bed_file.csv' 
                outfile=f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_by_allbins_max_no_layer_limited_gene.h5ad'
                if ice_type=='KR':
                    gene_vector_file = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_by_allbins_max.h5'
                else:
                    gene_vector_file = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_by_allbins_none_max.h5'
                if species=='mouse':
                    gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
                else:
                    gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 
                get_input_matrix(process_type, marker_list_input_dict[species], df_regions_bed, gene_vector_file, outfile, gene_annot_file)






In [4]:
from hicmatrix import HiCMatrix as hm
from hicmatrix.lib import MatrixFileHandler
import numpy as np
import pandas as pd
from scipy import stats, sparse
import bottleneck
from scipy.stats import mannwhitneyu
import h5py
import os.path
import gc
import os
import matplotlib.pyplot as plt
from pyranges import read_gtf


from umap import UMAP
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
import scipy.spatial as sp, scipy.cluster.hierarchy as hc

import seaborn as sns


import anndata as ad
import scanpy as sc




def add_layers_anndata(process_type, input_file_h5ad, gene_annot_file, species, SRP_name, resolution, base_folder, ice_type):


    bins_bed = pd.read_csv(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/regions_bed_file.csv', names=['chr', 'start', 'end'])
    bins_bed['bin_id'] = bins_bed.index.tolist()

    bins_bed.to_csv(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/regions_bed_file.tsv', index=False, header=False, sep='\t')
    if species == 'human':

        blacklist_file = f'{base_folder}/BICCN_enhancer_challenege/10XMultiome/Human/hg38-blacklist.v2.bed'
    else:
        blacklist_file = f'{base_folder}/BICCN_enhancer_challenege/10XMultiome/Mouse/mm10-blacklist.v2.bed'

    os.system(f"bedtools intersect -wo -b {blacklist_file} -a {base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/regions_bed_file.tsv > {base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/all_bin_blacklist.bed")
    blacklist_bins = pd.read_csv(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/all_bin_blacklist.bed', sep='\t', names=['d', 'd1', 'd2', 'bin_id', 'c', 'c1', 'c2', 'c3', 'c4'])
    
    
    adata = ad.read_h5ad(f'{input_file_h5ad}')

    data = adata.X + 0.0
    
    if resolution == '1kbp_raw':
    
        data = data.astype('float32')
        
    elif resolution == '10kbp_raw':
    
        data = data.astype('float32')
    else:
        data = data.astype('float64')
        
    np_of_rows = len(adata.obs_names.tolist())
    np_of_col = len(adata.var_names.tolist())
        
    

        
    
    nan_columns = blacklist_bins['bin_id'].tolist()

    data[:, nan_columns] = np.nan


    chr_list = bins_bed.drop_duplicates(subset=['chr'])['chr'].tolist()

    chrom_index_list  = {}
    for chrom in chr_list:
          st = bins_bed[bins_bed['chr'] == chrom]['bin_id'].tolist()[0]
          en = bins_bed[bins_bed['chr'] == chrom]['bin_id'].tolist()[-1]
          chrom_index_list[chrom] = list(range(st, en+1))

    chrom_index_list_intra = {}
    for chrom in chr_list:
        index_list = []
        for chrom2 in chr_list:
            if chrom2 != chrom:
                index_list.extend(chrom_index_list[chrom2])

        chrom_index_list_intra[chrom] = index_list

    gtf = read_gtf(gene_annot_file)
    genes = gtf.df.loc[gtf.df['Feature'] == 'gene'].copy()
    genes['gene_id'] = [x.split('.')[0] for x in genes['gene_id']]
    genes['gene_id'].drop_duplicates(inplace=True)

    if not genes['Chromosome'].str.startswith('chr').any():
        genes['Chromosome'] = [f'chr{x}' for x in genes['Chromosome']]

    genes  = genes.set_index('gene_id')

    genes = genes.loc[adata.obs_names.tolist(), :]
    
    genes = genes.reset_index()



    genes[['Chromosome', 'Start', 'End', 'gene_id']].to_csv(f'{base_folder}hi_c_data_processing/data_{species}/gene_info.tsv', index=False, header=False, sep='\t')


    os.system(f"bedtools intersect -wo -b {base_folder}hi_c_data_processing/data_{species}/gene_info.tsv -a {base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/regions_bed_file.tsv > {base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/gene_info_bin_id.tsv")
    gene_id_bins = pd.read_csv(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/gene_info_bin_id.tsv', sep='\t', names=['d', 'd1', 'd2', 'bin_id', 'c', 'st', 'end', 'gene_id', 'c4'])

    
    if process_type == 'intra':

        layer_value_list = [0, 1, 10, 100, 1000, 10000]
        layer_name_list = ['intra']*len(layer_value_list)

    if process_type == 'inter':
        layer_name_list = ['inter']
        layer_value_list = [0]

    if process_type == 'gw':
        layer_value_list = [0, 1, 10, 100, 1000, 10000]
        layer_name_list = ['intra']*len(layer_value_list)
        layer_name_list.append('inter')
        layer_value_list.append(0)



    for layer_type, dist in zip(layer_name_list, layer_value_list):
        
            adata_l = ad.AnnData(np.zeros((np_of_rows, np_of_col)))
        
            new_layer_name = f'{process_type}_{layer_type}_{dist}'
        
        #if new_layer_name in adata.layers:
        #    continue
        #else:

            mask = np.zeros_like(data, dtype=bool)

        

            for index, row in genes.iterrows():

                if layer_type == 'intra':
                    columns_to_mask = chrom_index_list_intra[row['Chromosome']]
                else:
                    columns_to_mask = chrom_index_list[row['Chromosome']]

                mask[index, columns_to_mask] = True

                if layer_type == 'intra':

                    start_index = gene_id_bins[gene_id_bins['gene_id'] == row['gene_id']]['bin_id'].min()

                    end_index = gene_id_bins[gene_id_bins['gene_id'] == row['gene_id']]['bin_id'].max()

                    mask[index, start_index:end_index+1]  = True

                    #for idx in [start_index, end_index]:
                    mask[index, max(0, start_index - dist):min(data.shape[1], end_index + dist+1)] = True




            data_layered = np.where(mask, np.nan, data)



            layer_name = f'{layer_type}_{dist}_raw'
            

            adata_l.layers[layer_name] = data_layered
            
            
            adata_l.obs_names = adata.obs_names.tolist()
            adata_l.var_names = adata.var_names.tolist()
            
            outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{layer_name}_by_allbins_max.h5ad'
            
            adata_l.write(outputfile_h5ad, compression="gzip")

            z_scores = stats.zscore(data_layered, axis=1, nan_policy='omit')


            clipped_z_scores = np.clip(z_scores, -10, 10)
            
            layer_name = f'{layer_type}_{dist}_z_scores'

            adata_l.layers[layer_name] = clipped_z_scores
            
            
            outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{layer_name}_by_allbins_max.h5ad'
            
            adata_l.write(outputfile_h5ad, compression="gzip")
            
            del z_scores
            del clipped_z_scores
            gc.collect()

            #data_plus_one = data_layered + 1

            #log_transformed_data = np.log1p(data_plus_one)

            del data_layered
            #del data_plus_one
            gc.collect()

            #layer_name = f'{process_type}_{layer_type}_{dist}_log_transformed'

            #adata.layers[layer_name] = log_transformed_data

            #z_scores = stats.zscore(log_transformed_data, axis=1, nan_policy='omit')

            #clipped_z_scores = np.clip(z_scores, -10, 10)



            #layer_name = f'{process_type}_{layer_type}_{dist}_log_transformed_z_scores'

            #adata.layers[layer_name] = clipped_z_scores

            #del z_scores
            #del log_transformed_data
            #del clipped_z_scores
            #gc.collect()

            
            

In [5]:
for species in ['human', 'mouse']:
    for process_type in ['intra', 'inter']:
        for resolution in ['250kbp_raw']:
            for ice_type in ['KR']:
            
                base_folder = '/grid/gillis/data_norepl/lohia/'
                SRP_name='aggregates'
                
                if ice_type == 'KR':
                    input_file_h5ad=f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_by_allbins_max_no_layer_limited_gene.h5ad'
                    
                else:
                    input_file_h5ad=f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_gw_{ice_type}_by_allbins_max_no_layer_limited_gene.h5ad' 
                if species=='mouse':
                    gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
                else:
                    gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 
                add_layers_anndata(process_type, input_file_h5ad, gene_annot_file, species, SRP_name, resolution, base_folder, ice_type)



In [8]:
from hicmatrix import HiCMatrix as hm
from hicmatrix.lib import MatrixFileHandler
import numpy as np
import pandas as pd
from scipy import stats, sparse
import bottleneck
from scipy.stats import mannwhitneyu
import h5py
import os.path
import gc
import os
import matplotlib.pyplot as plt
from pyranges import read_gtf
import os.path




from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
import scipy.spatial as sp, scipy.cluster.hierarchy as hc

import seaborn as sns


import anndata as ad
import scanpy as sc

# Assuming your data is organized as NumPy arrays
# gene_observation_matrix is genesXobservations
# gene_category_matrix is genesXcategories
# Both matrices are NumPy arrays

# Example gene_observation_matrix (5 genes, 3 observations) with NaN values


# Calculate the mean of genes for each category and observation, ignoring NaN values
def calculate_category_means_ignore_nan(gene_observation_matrix_df, gene_category_matrix_df):
    # Calculate mean for each category (axis=0) and each observation (axis=1), ignoring NaN values


    genes_intersect = gene_observation_matrix_df.index.intersection(gene_category_matrix_df.index)

    gene_observation_matrix_df =  gene_observation_matrix_df.loc[genes_intersect, :]
    gene_category_matrix_df = gene_category_matrix_df.loc[genes_intersect, :]

    gene_observation_matrix = gene_observation_matrix_df.values
    gene_category_matrix = gene_category_matrix_df.values

    category_counts = np.dot(gene_category_matrix.T, ~np.isnan(gene_observation_matrix))
    
    gene_observation_matrix_cleaned = np.nan_to_num(gene_observation_matrix, nan=0.0)
    
    category_sums = np.dot(gene_category_matrix.T, gene_observation_matrix_cleaned)
    
    # Calculate mean using only non-NaN values
    category_means = category_sums / category_counts
    
    # Replace NaN values in category_means with 0 where division by 0 occurred
    #category_means[np.isnan(category_means)] = 0.0
    
    return category_means, category_counts

# Call the function to calculate category means, ignoring NaN values


def calc_marker_matrix(marker_list,gene_list, no_of_markers=10,  drop_duplicates=True, shuffle_labels=False):
    
        
        marker_list = marker_list[marker_list['Ensembl_gene_identifier'].isin(gene_list)]

        marker_list = marker_list.sort_values(by=['rank']).drop_duplicates(subset=['cell_type', 'gene'])
        
        all_cell_types = marker_list.drop_duplicates(['cell_type'])['cell_type'].tolist()

        marker_list_list = []
        for group2 in all_cell_types:
                    m_tmp = marker_list[marker_list['cell_type']==group2].sort_values(by=['rank'])
                    m_tmp['rank_missing_gene'] = [x+1 for x in range(m_tmp.shape[0])]

                    marker_list_list.append(m_tmp)

        marker_list = pd.concat(marker_list_list)

        marker_list = marker_list[marker_list['rank_missing_gene']<=no_of_markers]

        marker_list['%recurrence'] = marker_list['recurrence'] / marker_list['n_datasets']
        marker_list['%recurrence'] = 1/marker_list['%recurrence']
        
        marker_list_copy = marker_list.copy()
        

        


        if drop_duplicates==True:

            marker_list = marker_list.sort_values(by=['rank', '%recurrence', 'auroc', 'rank_missing_gene']).drop_duplicates(subset=['Ensembl_gene_identifier'], keep=False)
        elif drop_duplicates=="one_copy":
            marker_list = marker_list.sort_values(by=['rank', '%recurrence', 'auroc', 'rank_missing_gene']).drop_duplicates(subset=['Ensembl_gene_identifier'])
        else:
            pass
        
        if shuffle_labels == True:
            

            shuffled_Ensembl_gene_identifier = marker_list['Ensembl_gene_identifier'].sample(frac=1, replace=False, random_state=42).reset_index(drop=True)


            marker_list['Ensembl_gene_identifier'] = shuffled_Ensembl_gene_identifier.tolist()
            
        else:
            pass


        df2_list = []
        for group2 in all_cell_types:
                    
                    m_tmp = marker_list[marker_list['cell_type']==group2]
                    #if number_of_times == 1:
                    df2_list.append(m_tmp)
                    #else:
                    #    random_indices = np.random.choice(m_tmp.index, size=bootstarp_size, replace=True)
                    #    bootstrap_sample = m_tmp.loc[random_indices]
                    #    df2_list.append(bootstrap_sample)

        marker_list=pd.concat(df2_list)
        marker_list_copy['rank'] = 0
        marker_list = pd.concat([marker_list, marker_list_copy])
        
        

        marker_table = marker_list.pivot_table(index='Ensembl_gene_identifier', columns='cell_type', values='rank', aggfunc='sum')

        marker_table.fillna(0, inplace=True)

        marker_table[marker_table != 0] = 1

        

        return marker_table
        

#for each marker-list and input file , I can make one output file

def calc_mean_profile(marker_name, base_folder, species, input_file_h5ad, process_type,  ice_type, dist, layer_name):
    
        if marker_name == 'GABAergic':
            marker_list = pd.read_csv(f'{base_folder}/hi_c_data_processing/{species}_brain_class.csv')
            marker_list = marker_list[marker_list['group']==marker_name]
            
        elif marker_name == 'Glutamatergic':
            marker_list = pd.read_csv(f'{base_folder}/hi_c_data_processing/{species}_brain_class.csv')
            marker_list = marker_list[marker_list['group']==marker_name]
        elif marker_name == 'test':
            marker_list = pd.read_csv(f'{base_folder}/hi_c_data_processing/{species}_brain_class.csv')
            marker_list = marker_list[marker_list['cell_type'].isin(['L6b', 'L5 IT'])]
        
        cell_type_order = marker_list['cell_type'].drop_duplicates().tolist()



        
        

        adata = ad.read_h5ad(f'{input_file_h5ad}', backed='r')
        
        np_of_col = adata.X.shape[1]
        np_of_rows = len(cell_type_order)
        
        #adata_l = ad.AnnData(np.zeros((np_of_rows, np_of_col)))
        
        layer_names = adata.layers.keys()
        no_of_markers_list = [1,2,3,4,5,6,7,8,9,10,11,12,13,15,17,19,21,23,25,29,33,37,41,46,50,58,65,73,82,92,100,115,129,144,150,162,181,200,227,250,284,300,356,400,446,500]     
        no_of_markers_list = [200]
        for given_layer in layer_names:
            for drop_duplicates in [False]:
                    for shuf in [False]:
                        
                        for no_of_markers in no_of_markers_list:
                            
                                fname = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean.h5ad'
                            
                                if os.path.isfile(fname):
                                    continue
                                adata_l = ad.AnnData(np.zeros((np_of_rows, np_of_col)))
                        
                            
                                

                                gene_list = adata.obs_names.tolist()

                                gene_observation_matrix_dataframe = adata.to_df(layer=given_layer)

                                gene_category_dataframe = calc_marker_matrix(marker_list, gene_list, no_of_markers=no_of_markers,  drop_duplicates=drop_duplicates, shuffle_labels=shuf)

                                gene_category_dataframe = gene_category_dataframe.loc[:,cell_type_order]

                                category_means, category_counts = calculate_category_means_ignore_nan(gene_observation_matrix_dataframe, gene_category_dataframe)

                                l_n = f'mean'

                                adata_l.layers[l_n] = category_means

                                l_n = f'counts'

                                adata_l.layers[l_n] = category_counts
                                
                                #z_scores = stats.zscore(category_means, axis=0, nan_policy='omit')
                                #l_n = f'{given_layer}_{no_of_markers}_{drop_duplicates}_{shuf}_mean_scaled'
                                #adata_l.layers[l_n] = z_scores
                                
                                #z_scores = stats.zscore(category_counts, axis=0, nan_policy='omit')
                                #l_n = f'{given_layer}_{no_of_markers}_{drop_duplicates}_{shuf}_counts_scaled'
                                #adata_l.layers[l_n] = z_scores


                                adata_l.obs_names = cell_type_order
                                adata_l.var_names = adata.var_names.tolist()

                                outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean.h5ad'

                                adata_l.write(outputfile_h5ad, compression="gzip")








In [9]:
#updated calc mean profile

In [6]:
from hicmatrix import HiCMatrix as hm
from hicmatrix.lib import MatrixFileHandler
import numpy as np
import pandas as pd
from scipy import stats, sparse
import bottleneck
from scipy.stats import mannwhitneyu
import h5py
import os.path
import gc
import os
import matplotlib.pyplot as plt
from pyranges import read_gtf
import os.path




from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
import scipy.spatial as sp, scipy.cluster.hierarchy as hc

import seaborn as sns


import anndata as ad
import scanpy as sc

# Assuming your data is organized as NumPy arrays
# gene_observation_matrix is genesXobservations
# gene_category_matrix is genesXcategories
# Both matrices are NumPy arrays

# Example gene_observation_matrix (5 genes, 3 observations) with NaN values


# Calculate the mean of genes for each category and observation, ignoring NaN values
def calculate_category_means_ignore_nan(gene_observation_matrix_df, gene_category_matrix_df):
    # Calculate mean for each category (axis=0) and each observation (axis=1), ignoring NaN values


    genes_intersect = gene_observation_matrix_df.index.intersection(gene_category_matrix_df.index)

    gene_observation_matrix_df =  gene_observation_matrix_df.loc[genes_intersect, :]
    gene_category_matrix_df = gene_category_matrix_df.loc[genes_intersect, :]

    gene_observation_matrix = gene_observation_matrix_df.values
    gene_category_matrix = gene_category_matrix_df.values

    category_counts = np.dot(gene_category_matrix.T, ~np.isnan(gene_observation_matrix))
    
    gene_observation_matrix_cleaned = np.nan_to_num(gene_observation_matrix, nan=0.0)
    
    category_sums = np.dot(gene_category_matrix.T, gene_observation_matrix_cleaned)
    
    # Calculate mean using only non-NaN values
    category_means = category_sums / category_counts
    
    # Replace NaN values in category_means with 0 where division by 0 occurred
    #category_means[np.isnan(category_means)] = 0.0
    
    return category_means, category_counts

# Call the function to calculate category means, ignoring NaN values


def calc_marker_matrix(marker_list,gene_list, no_of_markers=10,  drop_duplicates=True, shuffle_labels=False):
    
        
        marker_list = marker_list[marker_list['Ensembl_gene_identifier'].isin(gene_list)]

        marker_list = marker_list.sort_values(by=['rank']).drop_duplicates(subset=['cell_type', 'gene'])
        
        all_cell_types = marker_list.drop_duplicates(['cell_type'])['cell_type'].tolist()

        marker_list_list = []
        for group2 in all_cell_types:
                    m_tmp = marker_list[marker_list['cell_type']==group2].sort_values(by=['rank'])
                    m_tmp['rank_missing_gene'] = [x+1 for x in range(m_tmp.shape[0])]

                    marker_list_list.append(m_tmp)

        marker_list = pd.concat(marker_list_list)

        marker_list = marker_list[marker_list['rank_missing_gene']<=no_of_markers]

        marker_list['%recurrence'] = marker_list['recurrence'] / marker_list['n_datasets']
        marker_list['%recurrence'] = 1/marker_list['%recurrence']
        
        marker_list_copy = marker_list.copy()
        

        


        if drop_duplicates==True:

            marker_list = marker_list.sort_values(by=['rank', '%recurrence', 'auroc', 'rank_missing_gene']).drop_duplicates(subset=['Ensembl_gene_identifier'], keep=False)
        elif drop_duplicates=="one_copy":
            marker_list = marker_list.sort_values(by=['rank', '%recurrence', 'auroc', 'rank_missing_gene']).drop_duplicates(subset=['Ensembl_gene_identifier'])
        else:
            pass
        
        if shuffle_labels == True:
            

            shuffled_Ensembl_gene_identifier = marker_list['Ensembl_gene_identifier'].sample(frac=1, replace=False, random_state=42).reset_index(drop=True)


            marker_list['Ensembl_gene_identifier'] = shuffled_Ensembl_gene_identifier.tolist()
            
        else:
            pass


        df2_list = []
        for group2 in all_cell_types:
                    
                    m_tmp = marker_list[marker_list['cell_type']==group2]
                    #if number_of_times == 1:
                    df2_list.append(m_tmp)
                    #else:
                    #    random_indices = np.random.choice(m_tmp.index, size=bootstarp_size, replace=True)
                    #    bootstrap_sample = m_tmp.loc[random_indices]
                    #    df2_list.append(bootstrap_sample)

        marker_list=pd.concat(df2_list)
        marker_list_copy['rank'] = 0
        marker_list = pd.concat([marker_list, marker_list_copy])
        
        

        marker_table = marker_list.pivot_table(index='Ensembl_gene_identifier', columns='cell_type', values='rank', aggfunc='sum')

        marker_table.fillna(0, inplace=True)

        marker_table[marker_table != 0] = 1

        

        return marker_table
        

#for each marker-list and input file , I can make one output file

def calc_mean_profile(marker_name, base_folder, species, input_file_h5ad, process_type,  ice_type, dist, layer_name):

        marker_list= pd.read_csv(f'{base_folder}/hi_c_data_processing/{species}_{marker_name}.csv')
        cell_type_order = marker_list['cell_type'].drop_duplicates().tolist()



        
        

        adata = ad.read_h5ad(f'{input_file_h5ad}', backed='r')
        
        np_of_col = adata.X.shape[1]
        np_of_rows = len(cell_type_order)
        
        #adata_l = ad.AnnData(np.zeros((np_of_rows, np_of_col)))
        
        layer_names = adata.layers.keys()
        no_of_markers_list = [1,2,3,4,5,6,7,8,9,10,11,12,13,15,17,19,21,23,25,29,33,37,41,46,50,58,65,73,82,92,100,115,129,144,150,162,181,200,227,250,284,300,356,400,446,500]     
        #no_of_markers_list = [200]
        #for given_layer in layer_names:
        print (layer_names)
        
        for given_layer in [layer_name]:
            for drop_duplicates in [False, True]:
                    for shuf in [True, False]:
                        
                        for no_of_markers in no_of_markers_list:
                            
                                outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/{marker_name}/mean/hic_gene_{ice_type}_{given_layer}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean.h5ad'
                            
                                #fname = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean.h5ad'
                            
                                if os.path.isfile(outputfile_h5ad):
                                    continue
                                adata_l = ad.AnnData(np.zeros((np_of_rows, np_of_col)))
                        
                            
                                

                                gene_list = adata.obs_names.tolist()

                                gene_observation_matrix_dataframe = adata.to_df(layer=given_layer)

                                gene_category_dataframe = calc_marker_matrix(marker_list, gene_list, no_of_markers=no_of_markers,  drop_duplicates=drop_duplicates, shuffle_labels=shuf)

                                gene_category_dataframe = gene_category_dataframe.loc[:,cell_type_order]

                                category_means, category_counts = calculate_category_means_ignore_nan(gene_observation_matrix_dataframe, gene_category_dataframe)

                                l_n = f'mean'

                                adata_l.layers[l_n] = category_means

                                l_n = f'counts'

                                adata_l.layers[l_n] = category_counts
                                
                                #z_scores = stats.zscore(category_means, axis=0, nan_policy='omit')
                                #l_n = f'{given_layer}_{no_of_markers}_{drop_duplicates}_{shuf}_mean_scaled'
                                #adata_l.layers[l_n] = z_scores
                                
                                #z_scores = stats.zscore(category_counts, axis=0, nan_policy='omit')
                                #l_n = f'{given_layer}_{no_of_markers}_{drop_duplicates}_{shuf}_counts_scaled'
                                #adata_l.layers[l_n] = z_scores


                                adata_l.obs_names = cell_type_order
                                adata_l.var_names = adata.var_names.tolist()
                                
                                directory=f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/{marker_name}/mean'
                                
                                if not os.path.exists(directory):
                                    os.makedirs(directory)
                                    
                                #print (outputfile_h5ad)

                                outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/{marker_name}/mean/hic_gene_{ice_type}_{given_layer}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean.h5ad'

                                adata_l.write(outputfile_h5ad, compression="gzip")








In [13]:

for process_type in ['intra', 'inter']:
    for resolution in ['10kbp_raw', '40kbp_raw', '100kbp_raw', '250kbp_raw']:
        for dist in [0]:
            for species in ['human', 'mouse']:
                for marker_name in ['brain_class']:
                    layer_name = 'z_scores'
                    layer_name = f'{process_type}_{dist}_z_scores'
                    base_folder = '/grid/gillis/data_norepl/lohia/'
                    SRP_name='aggregates'
                    ice_type='KR'
                    input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{layer_name}_by_allbins_max.h5ad'
                    if species=='mouse':
                        gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
                    else:
                        gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 
                    
                    
                    calc_mean_profile(marker_name, base_folder, species, input_file_h5ad, process_type,  ice_type, dist, layer_name)



KeysView(Layers with keys: intra_0_raw, intra_0_z_scores)
KeysView(Layers with keys: intra_0_raw, intra_0_z_scores)
KeysView(Layers with keys: intra_0_raw, intra_0_z_scores)


<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts

KeysView(Layers with keys: intra_0_raw, intra_0_z_scores)


<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts

KeysView(Layers with keys: intra_0_raw, intra_0_z_scores)


...

KeysView(Layers with keys: inter_0_raw, inter_0_z_scores)


<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts

KeysView(Layers with keys: inter_0_raw, inter_0_z_scores)


<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts

KeysView(Layers with keys: inter_0_raw, inter_0_z_scores)
KeysView(Layers with keys: inter_0_raw, inter_0_z_scores)


In [ ]:
for process_type in ['intra', 'inter']:
    for resolution in ['10kbp_raw', '40kbp_raw', '100kbp_raw', '250kbp_raw']:
        for dist in [0]:
            for species in ['human']:
                for marker_name in ['brain_heart']:
                    layer_name = 'z_scores'
                    layer_name = f'{process_type}_{dist}_z_scores'
                    base_folder = '/grid/gillis/data_norepl/lohia/'
                    SRP_name='aggregates'
                    ice_type='KR'
                    input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{layer_name}_by_allbins_max.h5ad'
                    if species=='mouse':
                        gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
                    else:
                        gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 
                    
                    
                    calc_mean_profile(marker_name, base_folder, species, input_file_h5ad, process_type,  ice_type, dist, layer_name)



/home/lohia/miniconda3/envs/hicexplorer/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3361: DtypeWarning: Columns (13,14,15,16,17,18,19,20,21) have mixed types.Specify dtype option on import or set low_memory=False.
  if (await self.run_code(code, result,  async_=asy)):


KeysView(Layers with keys: intra_0_raw, intra_0_z_scores)


<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts

KeysView(Layers with keys: intra_0_raw, intra_0_z_scores)


<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts

...

<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts

KeysView(Layers with keys: inter_0_raw, inter_0_z_scores)


<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts

KeysView(Layers with keys: inter_0_raw, inter_0_z_scores)


<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts
<ipython-input-6-66ba040d5da4>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts

In [ ]:
for process_type in ['intra', 'inter']:
    for resolution in ['10kbp_raw', '40kbp_raw', '100kbp_raw', '250kbp_raw']:
        for dist in [0]:
            for species in ['human']:
                for marker_name in ['brain_blood']:
                    layer_name = 'z_scores'
                    layer_name = f'{process_type}_{dist}_z_scores'
                    base_folder = '/grid/gillis/data_norepl/lohia/'
                    SRP_name='aggregates'
                    ice_type='KR'
                    input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{layer_name}_by_allbins_max.h5ad'
                    if species=='mouse':
                        gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
                    else:
                        gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 
                    
                    
                    calc_mean_profile(marker_name, base_folder, species, input_file_h5ad, process_type,  ice_type, dist, layer_name)



In [13]:
input_path_template = '/grid/gillis/data_norepl/lohia/hi_c_data_processing/data_human/aggregates/250kbp_raw/max/hic_gene_gw_none_by_allbins_max.h5ad'

adata = ad.read_h5ad(input_path_template, backed='r')


In [ ]:
for process_type in ['inter']:
    for resolution in ['10kbp_raw']:
        for dist in [0]:
            for species in ['mouse', 'human']:
                for marker_name in ['GABAergic', 'Glutamatergic']:
                    layer_name = 'z_scores'
                    base_folder = '/grid/gillis/data_norepl/lohia/'
                    SRP_name='aggregates'
                    ice_type='KR'
                    input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{process_type}_{dist}_{layer_name}_by_allbins_max.h5ad'
                    if species=='mouse':
                        gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
                    else:
                        gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 
                    calc_mean_profile(marker_name, base_folder, species, input_file_h5ad, process_type,  ice_type, dist, layer_name)



In [6]:
for process_type in ['inter']:
    for resolution in ['10kbp_raw']:
        for dist in [0]:
            for species in ['human']:
                for marker_name in ['test']:
                    layer_name = 'z_scores'
                    base_folder = '/grid/gillis/data_norepl/lohia/'
                    SRP_name='aggregates'
                    ice_type='KR'
                    input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{process_type}_{dist}_{layer_name}_by_allbins_max.h5ad'
                    if species=='mouse':
                        gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
                    else:
                        gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 
                    calc_mean_profile(marker_name, base_folder, species, input_file_h5ad, process_type,  ice_type, dist, layer_name)



<ipython-input-5-c344a4610a86>:57: RuntimeWarning: invalid value encountered in true_divide
  category_means = category_sums / category_counts


In [4]:
def calc_marker_number(marker_name, base_folder, species, input_file_h5ad, process_type,  ice_type, dist, layer_name):
    
        if marker_name == 'GABAergic':
            marker_list = pd.read_csv(f'{base_folder}/hi_c_data_processing/{species}_brain_class.csv')
            marker_list = marker_list[marker_list['group']==marker_name]
            
        elif marker_name == 'Glutamatergic':
            marker_list = pd.read_csv(f'{base_folder}/hi_c_data_processing/{species}_brain_class.csv')
            marker_list = marker_list[marker_list['group']==marker_name]

        else:
            marker_list = pd.read_csv(f'{base_folder}/hi_c_data_processing/{species}_{marker_name}.csv') 
        
        cell_type_order = marker_list['cell_type'].drop_duplicates().tolist()



        
        

        adata = ad.read_h5ad(f'{input_file_h5ad}', backed='r')
        
        np_of_col = adata.X.shape[1]
        np_of_rows = len(cell_type_order)
        
        #adata_l = ad.AnnData(np.zeros((np_of_rows, np_of_col)))
        
        layer_names = adata.layers.keys()
        no_of_markers_list = [1,2,3,4,5,6,7,8,9,10,11,12,13,15,17,19,21,23,25,29,33,37,41,46,50,58,65,73,82,92,100,115,129,144,150,162,181,200,227,250,284,300,356,400,446,500]     
        for given_layer in layer_names:
            for drop_duplicates in [True]:
                    for shuf in [False]:
                        
                        for no_of_markers in no_of_markers_list:
                            
                                fname = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_true_no_of_markers.h5ad'
                            
                                if os.path.isfile(fname):
                                    continue
                                adata_l = ad.AnnData(np.zeros((np_of_rows, np_of_col)))
                        
                                gene_list = adata.obs_names.tolist()

                                gene_observation_matrix_dataframe = adata.to_df(layer=given_layer)

                                gene_category_dataframe = calc_marker_matrix(marker_list, gene_list, no_of_markers=no_of_markers,  drop_duplicates=drop_duplicates, shuffle_labels=shuf)

                                gene_category_dataframe = gene_category_dataframe.loc[:,cell_type_order]

                                gene_category_dataframe.to_csv(fname)




In [6]:
for process_type in ['inter']:
    for resolution in ['10kbp_raw']:
        for dist in [0]:
            for species in ['mouse', 'human']:
                for marker_name in ['Glutamatergic', 'brain_heart']:
                    layer_name = 'z_scores'
                    base_folder = '/grid/gillis/data_norepl/lohia/'
                    SRP_name='aggregates'
                    ice_type='KR'
                    input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{process_type}_{dist}_{layer_name}_by_allbins_max.h5ad'
                    if species=='mouse':
                        gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
                    else:
                        gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 
                    calc_marker_number(marker_name, base_folder, species, input_file_h5ad, process_type,  ice_type, dist, layer_name)



In [13]:
#cross species correlation
from hicmatrix import HiCMatrix as hm
from hicmatrix.lib import MatrixFileHandler
import numpy as np
import pandas as pd
from scipy import stats, sparse
import bottleneck
from scipy.stats import mannwhitneyu
import h5py
import os.path
import gc
import os
import matplotlib.pyplot as plt
from pyranges import read_gtf


from umap import UMAP
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
import scipy.spatial as sp, scipy.cluster.hierarchy as hc

import seaborn as sns


import anndata as ad
import scanpy as sc


#egad function

import numpy as np
import pandas as pd
from scipy import stats, sparse
import bottleneck




def calculate_pearson_correlation(df, df_b, corr_method):
    # Perform bin intersection
    bins_intersect = set(df.columns.tolist()).intersection(set(df_b.columns.tolist()))
    df = df.loc[:, bins_intersect]
    #df = df.fillna(0)
    #df_b = df_b.fillna(0)
    df_b = df_b.loc[:, bins_intersect]


    # Z-score normalization
    df_b_z = stats.zscore(df_b, axis=0, nan_policy='omit')
    df_b_z = pd.DataFrame(df_b_z, index=df_b.index.tolist(), columns=df_b.columns)
    df_b_z['cell_type'] = df_b_z.index.tolist()
    df_b_z = df_b_z.set_index(['cell_type'])

    df_z = stats.zscore(df, axis=0, nan_policy='omit')
    df_z = pd.DataFrame(df_z, index=df.index.tolist(), columns=df.columns)
    df_z['cell_type'] = df_z.index.tolist()
    df_z['cell_type'] = [x + '_hic' for x in df_z['cell_type']]
    df_z = df_z.set_index(['cell_type'])
    

    # Concatenate dataframes
    df_corr = pd.concat([df_b_z, df_z])

    
    
    #df_corr = df_corr.dropna(axis=1, how='all')
    #df_corr = df_corr.dropna(axis=1)
    
    #df_corr = df_corr.set_index(['cell_type'])

            
    #features_sc = stats.zscore(df_corr, axis=0, nan_policy='omit')
    
    #features_sc = features_sc.dropna(how='all', axis=1).fillna(0)
    
    #features_sc = features_sc.dropna(how='all', axis=1)
    
                
    #df_dist_df = features_sc.T.corr(min_periods=200, method=corr_method)
    df_dist_df = df_corr.T.corr(min_periods=10, method=corr_method)



    return df_dist_df


def calculate_auc_nan(df_dist_df, tp):
    df_jac_subset = df_dist_df.values
    df_exp_subset = tp.values

    coodinates_1 = np.where(np.isnan(df_jac_subset))
    coodinates_2 = np.where(np.isnan(df_exp_subset))

    x_coo = coodinates_1[0].tolist() + coodinates_2[0].tolist()
    y_coo = coodinates_1[1].tolist() + coodinates_2[1].tolist()

    df_jac_subset[x_coo, y_coo] = np.nan
    df_exp_subset[x_coo, y_coo] = np.nan

    predicts2 = bottleneck.nanrankdata(df_jac_subset, axis=1)

    tp = df_exp_subset.copy()
    tn = 1 - tp

    pos_rank_sum = tp * predicts2
    auc_array = (((np.nansum(pos_rank_sum, axis=1) / (np.nansum(tp, axis=1))) - (np.nansum(tp, axis=1) + 1) / 2)) / np.nansum(tn, axis=1)

    df_auc = pd.DataFrame({'cell_type': df_dist_df.index.tolist(), 'AUC': auc_array})

    return df_auc


        

#for each marker-list and input file , I can make one output file

def calc_pair_corr(input_file_h5ad_a, input_file_h5ad_b, file_b_species, outputfile_h5ad, resolution, base_folder, SRP_name):

        adata = ad.read_h5ad(f'{input_file_h5ad_a}', backed='r')
        adata_b = ad.read_h5ad(f'{input_file_h5ad_b}', backed='r')
        df_b = adata_b.to_df()

        df = adata.to_df()

        cell_type_intersect = df.index.intersection(df_b.index)




        species_input='mouse'
        species_output='human'
        
        if file_b_species == 'mouse':
            species_input='mouse'
            species_output='human'
        else:
            species_input='human'
            species_output='mouse'
        
        full_input_path = f'{base_folder}/hi_c_data_processing/data_{species_input}/{SRP_name}/{resolution}/max/'
        
        full_target_path = f'{base_folder}/hi_c_data_processing/data_{species_output}/{SRP_name}/{resolution}/max/'
        if species_input=='mouse':
            chain_file = 'mm10ToHg38.over.chain.gz'
        else:
            chain_file = 'hg38ToMm10.over.chain.gz'
        for minmatch in [0.5]:

            #os.system(f"{base_folder}/hi_c_data_processing/software/liftOver -minMatch={minmatch} {full_input_path}/regions_bed_file.tsv {base_folder}/hi_c_data_processing/software/{chain_file} {full_input_path}/minmatch{minmatch}_{species_input}_to_{species_output}.bed u")

            #os.system(f"~/.conda/envs/hicexplorer/bin/bedtools intersect -wo -b {full_input_path}/minmatch{minmatch}_{species_input}_to_{species_output}.bed -a {full_target_path}/regions_bed_file.tsv > {full_target_path}/minmatch{minmatch}_{species_input}_to_{species_output}_matched.bed")

            if species_output=='human':

                df_human_mouse_bins = pd.read_csv(f'{full_target_path}/minmatch{minmatch}_{species_input}_to_{species_output}_matched.bed', sep='\t', names=['a', 'b', 'c', 'human_bin', 'a1', 'b1', 'c1', 'mouse_bin', 'overlap'])
            else:
                df_human_mouse_bins = pd.read_csv(f'{full_target_path}/minmatch{minmatch}_{species_input}_to_{species_output}_matched.bed', sep='\t', names=['a', 'b', 'c', 'mouse_bin', 'a1', 'b1', 'c1', 'human_bin', 'overlap'])

        #correct bin_id to correct bin_id

        df_human_mouse_bins['mouse_bin'] = [f"bin_{i}" for i in df_human_mouse_bins['mouse_bin'].tolist()]
        df_human_mouse_bins['human_bin'] = [f"bin_{i}" for i in df_human_mouse_bins['human_bin'].tolist()]


        dk_human = df.copy()
        dk_mouse = df_b.copy()

        df_human_mouse_bins  = df_human_mouse_bins[df_human_mouse_bins['mouse_bin'].isin(dk_mouse.T.index.tolist())]
        df_human_mouse_bins  = df_human_mouse_bins[df_human_mouse_bins['human_bin'].isin(dk_human.T.index.tolist())]
                

        np_of_col = len(cell_type_intersect)*2
        np_of_rows = len(cell_type_intersect)*2
        
        adata_l = ad.AnnData(np.zeros((np_of_rows, np_of_col)))

        
        layer_names = adata.layers.keys()    
        for corr_method in ['pearson']:
                        for given_layer in layer_names:


                                df = adata.to_df(layer=given_layer)

                                df = df.loc[cell_type_intersect,:]

                                df_b = adata_b.to_df(layer=given_layer)

                                df_b = df_b.loc[cell_type_intersect,:]


                                df = df.loc[:,df_human_mouse_bins['human_bin'].tolist()]

                                df = df.T
                                df.index = df_human_mouse_bins['mouse_bin'].tolist()
                                df = df.T
                                df_b = df_b.loc[:,df_human_mouse_bins['mouse_bin'].tolist()]




                                df_corr_real_names = calculate_pearson_correlation(df, df_b, corr_method)

                                l_n = f'{given_layer}_{corr_method}'

                                adata_l.layers[l_n] = df_corr_real_names

                                # Perform cell type intersection
                                #cell_type_intersect = df.index.intersection(df_b.index)

                                hic_cell_type = [x + '_hic' for x in cell_type_intersect]

                                df_corr = df_corr_real_names.loc[cell_type_intersect,:]
                            
                                df_corr = df_corr[hic_cell_type]

                                #df_corr  = df_corr.fillna(0)

                                #df_corr += abs(df_corr.min().min())

                                given_dict = dict(zip(df_corr.index.tolist(), df_corr.index.tolist()))

                                n = len(given_dict.keys())

                                tp_class = np.zeros((n, n))

                                # Fill the diagonal elements with 1
                                np.fill_diagonal(tp_class, 1)

                                df_tp_class = pd.DataFrame(tp_class, index=given_dict.keys(), columns=given_dict.values())

                                for key, value in given_dict.items():
                                    df_tp_class.loc[key, value] = 1
                            
                                df_tp_class = df_tp_class.loc[df_corr.index.tolist(), :]
                                    
                                    
                                df_exp = calculate_auc_nan(df_corr, df_tp_class)

                                adata_l.uns[l_n] = df_exp



        adata_l.obs_names = df_corr_real_names.index.tolist()
        adata_l.var_names = df_corr_real_names.columns.tolist()

        adata_l.write(outputfile_h5ad, compression="gzip")





In [14]:

no_of_markers_list = [1,2,3,4,5,6,7,8,9,10,11,12,13,15,17,19,21,23,25,29,33,37,41,46,50,58,65,73,82,92,100,115,129,144,150,162,181,200,227,250,284,300,356,400,446,500]     
#no_of_markers_list = [200]   
for no_of_markers in no_of_markers_list:

    for species in ['human']:
        for process_type in ['intra']:
            for resolution in ['1kbp_raw']:
                for shuf in [True, False]:
                    for drop_duplicates in [False, True]:
                        for marker_name in ['brain_class']:
                                dist = 0
                                layer_name = 'z_scores'
                                base_folder = '/grid/gillis/data_norepl/lohia/'
                                SRP_name='aggregates'
                                ice_type='KR'

                                if species=='mouse':
                                    gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
                                else:
                                    gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 

                                input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean.h5ad'
                                outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean_cross_species.h5ad'

                                if species == 'human':
                                    species_b = 'mouse'
                                input_file_h5ad_b = f'{base_folder}/hi_c_data_processing/data_{species_b}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean.h5ad'
                                #calc_pair_corr(input_file_h5ad, input_file_h5ad_b, species_b, outputfile_h5ad, marker_name)
                                if os.path.isfile(outputfile_h5ad):
                                    pass
                                else:
                                    calc_pair_corr(input_file_h5ad, input_file_h5ad_b, species_b, outputfile_h5ad, resolution, base_folder, SRP_name)


<ipython-input-13-3b9e653854b9>:106: RuntimeWarning: invalid value encountered in true_divide
  auc_array = (((np.nansum(pos_rank_sum, axis=1) / (np.nansum(tp, axis=1))) - (np.nansum(tp, axis=1) + 1) / 2)) / np.nansum(tn, axis=1)


In [7]:
from hicmatrix import HiCMatrix as hm
from hicmatrix.lib import MatrixFileHandler
import numpy as np
import pandas as pd
from scipy import stats, sparse
import bottleneck
from scipy.stats import mannwhitneyu
import h5py
import os.path
import gc
import os
import matplotlib.pyplot as plt
from pyranges import read_gtf


from umap import UMAP
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
import scipy.spatial as sp, scipy.cluster.hierarchy as hc

import seaborn as sns


import anndata as ad
import scanpy as sc


#egad function

import numpy as np
import pandas as pd
from scipy import stats, sparse
import bottleneck




def calculate_pearson_correlation(df, df_b, corr_method):
    # Perform bin intersection
    bins_intersect = set(df.columns.tolist()).intersection(set(df_b.columns.tolist()))
    df = df.loc[:, bins_intersect]
    #df = df.fillna(0)
    #df_b = df_b.fillna(0)
    df_b = df_b.loc[:, bins_intersect]


    # Z-score normalization
    df_b_z = stats.zscore(df_b, axis=0, nan_policy='omit')
    df_b_z = pd.DataFrame(df_b_z, index=df_b.index.tolist(), columns=df_b.columns)
    df_b_z['cell_type'] = df_b_z.index.tolist()
    df_b_z = df_b_z.set_index(['cell_type'])

    df_z = stats.zscore(df, axis=0, nan_policy='omit')
    df_z = pd.DataFrame(df_z, index=df.index.tolist(), columns=df.columns)
    df_z['cell_type'] = df_z.index.tolist()
    df_z['cell_type'] = [x + '_hic' for x in df_z['cell_type']]
    df_z = df_z.set_index(['cell_type'])
    

    # Concatenate dataframes
    #print (df_b_z)
    #print (df_z)
    df_corr = pd.concat([df_b_z, df_z], axis=0)

    
    
    #df_corr = df_corr.dropna(axis=1, how='all')
    #df_corr = df_corr.dropna(axis=1)
    
    #df_corr = df_corr.set_index(['cell_type'])

            
    #features_sc = stats.zscore(df_corr, axis=0, nan_policy='omit')
    
    #features_sc = features_sc.dropna(how='all', axis=1).fillna(0)
    
    #features_sc = features_sc.dropna(how='all', axis=1)
    
                
    df_dist_df = df_corr.T.corr(min_periods=10, method=corr_method)



    return df_dist_df


def calculate_auc_nan(df_dist_df, tp):
    df_jac_subset = df_dist_df.values
    df_exp_subset = tp.values

    coodinates_1 = np.where(np.isnan(df_jac_subset))
    coodinates_2 = np.where(np.isnan(df_exp_subset))

    x_coo = coodinates_1[0].tolist() + coodinates_2[0].tolist()
    y_coo = coodinates_1[1].tolist() + coodinates_2[1].tolist()

    df_jac_subset[x_coo, y_coo] = np.nan
    df_exp_subset[x_coo, y_coo] = np.nan

    predicts2 = bottleneck.nanrankdata(df_jac_subset, axis=1)

    tp = df_exp_subset.copy()
    tn = 1 - tp

    pos_rank_sum = tp * predicts2
    auc_array = (((np.nansum(pos_rank_sum, axis=1) / (np.nansum(tp, axis=1))) - (np.nansum(tp, axis=1) + 1) / 2)) / np.nansum(tn, axis=1)

    df_auc = pd.DataFrame({'cell_type': df_dist_df.index.tolist(), 'AUC': auc_array})

    return df_auc

cell_type_map = {
 'Adipocyte' : 'Adipocytes',
 'Atrial Cardiomyocyte': 'Cardiomyocytes',
 'Ventricular Cardiomyocyte':'Immature_Cardiomyocytes',
 'Endothelial_Arterial': 'Endothelial' ,
 'Fibroblast': 'Fibroblasts',
 'Smooth Muscle': 'Smooth_Muscle_Cells',
 'Lymphocyte': 'Lymphoid_Immune_Cells',
 'Macrophage': 'Myeloid_Immune_Cells',
 'Nervous': 'Neuronal_Cells',}
        

#for each marker-list and input file , I can make one output file

def calc_pair_corr(input_file_h5ad, input_file_another_exp_h5ad, outputfile_h5ad, marker_name):
    

        adata = ad.read_h5ad(f'{input_file_h5ad}', backed='r')
        adata_b = ad.read_h5ad(f'{input_file_another_exp_h5ad}', backed='r')
        df_b = adata_b.to_df()
        
        if marker_name == 'heart':
            df_b.index = [cell_type_map[x] for x in cell_type_map]

        df = adata.to_df()

        cell_type_intersect = df.index.intersection(df_b.index)


        df_b = df_b.loc[cell_type_intersect,:]
        

        np_of_col = len(cell_type_intersect)*2
        np_of_rows = len(cell_type_intersect)*2
        
        adata_l = ad.AnnData(np.zeros((np_of_rows, np_of_col)))

        
        layer_names = adata.layers.keys()    
        for corr_method in ['pearson']:
                        for given_layer in layer_names:
                        #for given_layer in accepted_layer_list:
                        
                    
                                df = adata.to_df(layer=given_layer)

                                df = df.loc[cell_type_intersect,:]

                                df_corr_real_names = calculate_pearson_correlation(df, df_b, corr_method)

                                l_n = f'{given_layer}_{corr_method}'

                                adata_l.layers[l_n] = df_corr_real_names

                                # Perform cell type intersection
                                #cell_type_intersect = df.index.intersection(df_b.index)

                                hic_cell_type = [x + '_hic' for x in cell_type_intersect]

                                df_corr = df_corr_real_names.loc[cell_type_intersect,:]
                            
                                df_corr = df_corr[hic_cell_type]

                                #df_corr  = df_corr.fillna(0)

                                #df_corr += abs(df_corr.min().min())

                                given_dict = dict(zip(df_corr.index.tolist(), df_corr.index.tolist()))

                                n = len(given_dict.keys())

                                tp_class = np.zeros((n, n))

                                # Fill the diagonal elements with 1
                                np.fill_diagonal(tp_class, 1)

                                df_tp_class = pd.DataFrame(tp_class, index=given_dict.keys(), columns=given_dict.values())

                                for key, value in given_dict.items():
                                    df_tp_class.loc[key, value] = 1
                            
                                df_tp_class = df_tp_class.loc[df_corr.index.tolist(), :]
                                    
                                df_exp = calculate_auc_nan(df_corr, df_tp_class)

                                adata_l.uns[l_n] = df_exp



        adata_l.obs_names = df_corr_real_names.index.tolist()
        adata_l.var_names = df_corr_real_names.columns.tolist()

        adata_l.write(outputfile_h5ad, compression="gzip")


In [8]:
#no_of_markers_list = [1,2,3,4,5,6,7,8,9,10,11,12,13,15,17,19,21,23,25,29,33,37,41,46,50,58,65,73,82,92,100,115,129,144,150,162,181,200,227,250,284,300,356,400,446,500]     
no_of_markers_list = [200]
for no_of_markers in no_of_markers_list:
    for species in ['human']:
        for process_type in ['intra']:
            for resolution in ['1kbp_raw']:
                for shuf in [False]:
                    for drop_duplicates in [False]:
                        for marker_name in ['brain_class']:
                            for dist in [0]:
                                layer_name = 'z_scores'
                                base_folder = '/grid/gillis/data_norepl/lohia/'
                                SRP_name='aggregates'
                                ice_type='KR'
                                input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{process_type}_{dist}_{layer_name}_by_allbins_max.h5ad'
                                if species=='mouse':
                                    gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
                                else:
                                    gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 

                                input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean.h5ad'
                                input_file_another_exp_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/zemke_brain.h5ad'
                                outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean_atac.h5ad'


                                calc_pair_corr(input_file_h5ad, input_file_another_exp_h5ad, outputfile_h5ad, marker_name)



In [3]:

no_of_markers_list = [1,2,3,4,5,6,7,8,9,10,11,12,13,15,17,19,21,23,25,29,33,37,41,46,50,58,65,73,82,92,100,115,129,144,150,162,181,200,227,250,284,300,356,400,446,500]     
for no_of_markers in no_of_markers_list:




    for species in ['mouse']:
        for process_type in ['inter']:
            for resolution in ['10kbp_raw']:
                for shuf in [True, False]:
                    for drop_duplicates in [False]:
                        for marker_name in ['brain_class']:
                            for dist in [0]:
                                layer_name = 'z_scores'
                                base_folder = '/grid/gillis/data_norepl/lohia/'
                                SRP_name='aggregates'
                                ice_type='KR'
                                input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{process_type}_{dist}_{layer_name}_by_allbins_max.h5ad'
                                if species=='mouse':
                                    gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
                                else:
                                    gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 

                                #input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean.h5ad'
                                #input_file_another_exp_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/zemke_brain.h5ad'
                                #outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean_atac.h5ad'


                                #calc_pair_corr(input_file_h5ad, input_file_another_exp_h5ad, outputfile_h5ad, marker_name)

                                input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean.h5ad'                            
                                input_file_another_exp_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/compartment.h5ad'
                                outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean_compartment.h5ad'
                                
                                if os.path.isfile(outputfile_h5ad):
                                    os.remove(outputfile_h5ad)
                                    calc_pair_corr(input_file_h5ad, input_file_another_exp_h5ad, outputfile_h5ad, marker_name)
                                else:
                                    calc_pair_corr(input_file_h5ad, input_file_another_exp_h5ad, outputfile_h5ad, marker_name)





In [ ]:
    for species in ['mouse']:
        for process_type in ['inter']:
            for resolution in ['250kbp_raw', '100kbp_raw', '40kbp_raw', '10kbp_raw']:
                for shuf in [True, False]:
                    for drop_duplicates in [False]:
                        for marker_name in ['brain_class']:
                                dist = 0
                                layer_name = 'z_scores'
                                base_folder = '/grid/gillis/data_norepl/lohia/'
                                SRP_name='aggregates'
                                ice_type='KR'
                                input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{process_type}_{dist}_{layer_name}_by_allbins_max.h5ad'
                                if species=='mouse':
                                    gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
                                else:
                                    gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 

                                input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean.h5ad'
                                input_file_another_exp_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/zemke_brain.h5ad'
                                outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean_atac.h5ad'


                                calc_pair_corr(input_file_h5ad, input_file_another_exp_h5ad, outputfile_h5ad, marker_name)

                                input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean.h5ad'                            
                                input_file_another_exp_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/compartment.h5ad'
                                outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean_compartment.h5ad'
                                calc_pair_corr(input_file_h5ad, input_file_another_exp_h5ad, outputfile_h5ad, marker_name)










In [57]:
    for species in ['human']:
        for process_type in ['intra']:
            for resolution in ['250kbp_raw', '100kbp_raw', '40kbp_raw', '10kbp_raw']:
                for shuf in [True, False]:
                    for drop_duplicates in [False]:
                        for marker_name in ['brain_class']:
                            for dist in [0,1,10,100]:
                                layer_name = 'z_scores'
                                base_folder = '/grid/gillis/data_norepl/lohia/'
                                SRP_name='aggregates'
                                ice_type='KR'
                                input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{process_type}_{dist}_{layer_name}_by_allbins_max.h5ad'
                                if species=='mouse':
                                    gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
                                else:
                                    gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 

                                input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean.h5ad'
                                input_file_another_exp_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/zemke_brain.h5ad'
                                outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean_atac.h5ad'


                                calc_pair_corr(input_file_h5ad, input_file_another_exp_h5ad, outputfile_h5ad, marker_name)

                                #marker_name = 'heart'

                                #input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean.h5ad'
                                #input_file_another_exp_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/zemke_heart.h5ad'
                                #outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean_atac.h5ad'


                                #calc_pair_corr(input_file_h5ad, input_file_another_exp_h5ad, outputfile_h5ad, marker_name)




    for species in ['human']:
        for process_type in ['inter']:
            for resolution in ['250kbp_raw', '100kbp_raw', '40kbp_raw', '10kbp_raw']:
                for shuf in [True, False]:
                    for drop_duplicates in [False]:
                        for marker_name in ['brain_class']:
                                dist = 0
                                layer_name = 'z_scores'
                                base_folder = '/grid/gillis/data_norepl/lohia/'
                                SRP_name='aggregates'
                                ice_type='KR'
                                input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{process_type}_{dist}_{layer_name}_by_allbins_max.h5ad'
                                if species=='mouse':
                                    gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
                                else:
                                    gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 

                                input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean.h5ad'
                                input_file_another_exp_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/zemke_brain.h5ad'
                                outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean_atac.h5ad'


                                calc_pair_corr(input_file_h5ad, input_file_another_exp_h5ad, outputfile_h5ad, marker_name)

                                #marker_name = 'heart'

                                #input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean.h5ad'
                                #input_file_another_exp_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/zemke_heart.h5ad'
                                #outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean_atac.h5ad'


                                #calc_pair_corr(input_file_h5ad, input_file_another_exp_h5ad, outputfile_h5ad, marker_name)



OSError: Unable to create file (unable to truncate a file which is already open)

In [17]:
from hicmatrix import HiCMatrix as hm
from hicmatrix.lib import MatrixFileHandler
import numpy as np
import pandas as pd
from scipy import stats, sparse
import bottleneck
from scipy.stats import mannwhitneyu
import h5py
import os.path
import gc
import os
import matplotlib.pyplot as plt
from pyranges import read_gtf


from umap import UMAP

from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
import scipy.spatial as sp, scipy.cluster.hierarchy as hc

import seaborn as sns


import anndata as ad
import scanpy as sc

def get_atac_values(resolution):
    species='mouse'
    base_folder='/grid/gillis/data_norepl/lohia/'
    SRP_name='aggregates'

    cell_type_map = {'VLMC' : 'VLMC' ,
    'Micro-PVM' : 'MGC' ,
    'Astro' : 'ASC' ,
    'L2/3 IT' : 'L2_3_IT' ,
    'L5 IT' : 'L5_IT' ,
    'Oligo' : 'ODC' ,
    'Sst' : 'SST' ,
    'Pvalb' : 'PVALB' ,
    'Vip' : 'VIP' ,
    'Endo' : 'Endo' ,
    'Lamp5' : 'LAMP5' ,
    'Sncg' : 'SNCG' ,
    'L5/6 NP' : 'L5_6_NP' ,
    'L5 ET' : 'L5_ET' ,
    'L6 CT' : 'L6_CT' ,
    'L6b' :  'L6b' ,
    'Sst Chodl' : 'SST' ,
    'L6 IT' : 'L6_IT' 
    }



    df_marker = pd.read_csv(f'{base_folder}/BICCN_enhancer_challenege/catlas_ccre/mouse/marker_all_info.csv')

    df_marker = df_marker.drop_duplicates('group')

    class_dict = dict(zip(df_marker.group, df_marker.classt))

    df_atac_subclass_macs2 = pd.read_csv(f'{base_folder}/BICCN_enhancer_challenege/catlas_ccre/mouse/zemke_2023/Supplementary_Table_7.tsv', sep='\t')



    df_atac_subclass_macs2['chr'] = [x.split('-')[0] for x in df_atac_subclass_macs2['coord']]
    df_atac_subclass_macs2['st'] = [x.split('-')[1] for x in df_atac_subclass_macs2['coord']]
    df_atac_subclass_macs2['end'] = [x.split('-')[2] for x in df_atac_subclass_macs2['coord']]
    df_atac_subclass_macs2 = df_atac_subclass_macs2[~df_atac_subclass_macs2['chr'].isin(['chrX', 'chrY'])]
    df_atac_subclass_macs2['chr_num'] = [int(x.split('chr')[1]) for x in df_atac_subclass_macs2['chr']]
    df_atac_subclass_macs2['ste'] = df_atac_subclass_macs2['st'].astype('int')
    df_atac_subclass_macs2 = df_atac_subclass_macs2.sort_values(['chr_num', 'ste'])



    df_list = []
    for keyl in cell_type_map.keys():

        df_atac_subclass_macs2['gg'] = [1 if cell_type_map[keyl] in x else 0 for x in df_atac_subclass_macs2['celltype']]
        df = df_atac_subclass_macs2[df_atac_subclass_macs2['gg'] == 1]
        df['cell_type'] = keyl
        df_list.append(df[['chr', 'st', 'end', 'peak_id', 'cell_type']])
    df_Zemke2023_label = pd.concat(df_list)

    df_Zemke2023_label = df_Zemke2023_label.drop_duplicates()
    b_dir = f'{base_folder}/BICCN_enhancer_challenege/catlas_ccre/mouse/zemke_2023/'

    df_Zemke2023_label.to_csv(f'{b_dir}/all_cre_{resolution}.bed', index=False, header=False, sep='\t')

    os.system(f"~/.conda/envs/hicexplorer/bin/bedtools intersect -wo -b {b_dir}/all_cre_{resolution}.bed -a {base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/regions_bed_file.tsv > {b_dir}/all_cre_bins_{resolution}.bed")

    df_Zemke2023 = pd.read_csv(f'{b_dir}/all_cre_bins_{resolution}.bed', sep='\t', names=['chr', 'st', 'end', 'bin_id', 'p_chr', 'p_st', 'p_end', 'peak_label', 'cell_type', 'overlap' ])

    df_Zemke2023['rank'] = 1






    #df_Zemke2023 = df_Zemke2023[df_Zemke2023['overlap'] > 250]
    #df_Zemke2023 = df_Zemke2023.sort_values( by=['overlap'], ascending=False).drop_duplicates(subset=['bin_id'])

    #df_Zemke2023['cell_type'] = [class_dict[x] if x in class_dict.keys() else 'del' for x in df_Zemke2023['cell_type'].tolist()]

    df_Zemke2023_table = df_Zemke2023.pivot_table(index='bin_id', columns='cell_type', values='rank', aggfunc='sum')

    df_Zemke2023_table.fillna(0, inplace=True)

    df_Zemke2023_table[df_Zemke2023_table != 0] = 1

    df_Zemke2023_mouse = df_Zemke2023_table.T
    
    print (df_Zemke2023_mouse)

    #df_Zemke2023_mouse = df_Zemke2023_table[~df_Zemke2023_table.index.isin(['del'])]




    adata = ad.AnnData(df_Zemke2023_mouse)

    # Write AnnData object to a file

    #adata.obs_names = [f"gene_{i}" for i in gene_list]
    adata.var_names = [f"bin_{i}" for i in adata.var_names.tolist() ]

    z_scores = stats.zscore(adata.X, axis=0, nan_policy='omit')

    layer_name = f'z_scores_per_bin'

    adata.layers[layer_name] = z_scores

    adata.write_h5ad(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/zemke_brain.h5ad')  # Replace "your_output_file.h5ad" with your desired output file path








    #z_score_human
    species='human'

    cell_type_map = {'VLMC' : 'VLMC' ,
    'Micro-PVM' : 'MGC' ,
    'Astro' : 'ASC' ,
    'L2/3 IT' : 'L2_3_IT' ,
    'L5 IT' : 'L5_IT' ,
    'Oligo' : 'ODC' ,
    'Sst' : 'SST' ,
    'Pvalb' : 'PVALB' ,
    'Vip' : 'VIP' ,
    'Endo' : 'Endo' ,
    'Lamp5' : 'LAMP5' ,
    'Sncg' : 'SNCG' ,
    'L5/6 NP' : 'L5_6_NP' ,
    'L5 ET' : 'L5_ET' ,
    'L6 CT' : 'L6_CT' ,
    'L6b' :  'L6b' ,
    'Sst Chodl' : 'SST' ,
    'L6 IT' : 'L6_IT' 
    }

    df_atac_subclass_macs2 = pd.read_csv(f'{base_folder}/BICCN_enhancer_challenege/catlas_ccre/human/zemke_2023/Supplementary_Table_4.tsv', sep='\t')



    df_atac_subclass_macs2['chr'] = [x.split('-')[0] for x in df_atac_subclass_macs2['hg38_coord']]
    df_atac_subclass_macs2['st'] = [x.split('-')[1] for x in df_atac_subclass_macs2['hg38_coord']]
    df_atac_subclass_macs2['end'] = [x.split('-')[2] for x in df_atac_subclass_macs2['hg38_coord']]
    df_atac_subclass_macs2 = df_atac_subclass_macs2[~df_atac_subclass_macs2['chr'].isin(['chrX', 'chrY'])]
    df_atac_subclass_macs2['chr_num'] = [int(x.split('chr')[1]) for x in df_atac_subclass_macs2['chr']]
    df_atac_subclass_macs2['ste'] = df_atac_subclass_macs2['st'].astype('int')
    df_atac_subclass_macs2 = df_atac_subclass_macs2.sort_values(['chr_num', 'ste'])



    df_list = []
    for keyl in cell_type_map.keys():

        df_atac_subclass_macs2['gg'] = [1 if cell_type_map[keyl] in x else 0 for x in df_atac_subclass_macs2['celltype']]
        df = df_atac_subclass_macs2[df_atac_subclass_macs2['gg'] == 1]
        df['cell_type'] = keyl
        df_list.append(df[['chr', 'st', 'end', 'peak_id', 'cell_type']])
    df_Zemke2023_label = pd.concat(df_list)

    df_Zemke2023_label = df_Zemke2023_label.drop_duplicates()




    b_dir = f'{base_folder}/BICCN_enhancer_challenege/catlas_ccre/human/zemke_2023/'

    df_Zemke2023_label.to_csv(f'{b_dir}/all_cre_{resolution}.bed', index=False, header=False, sep='\t')


    os.system(f"~/.conda/envs/hicexplorer/bin/bedtools intersect -wo -b {b_dir}/all_cre_{resolution}.bed -a {base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/regions_bed_file.tsv > {b_dir}/all_cre_bins_{resolution}.bed")

    df_Zemke2023 = pd.read_csv(f'{b_dir}/all_cre_bins_{resolution}.bed', sep='\t', names=['chr', 'st', 'end', 'bin_id', 'p_chr', 'p_st', 'p_end', 'peak_label', 'cell_type', 'overlap' ])

    df_Zemke2023['rank'] = 1

    #df_Zemke2023 = df_Zemke2023[df_Zemke2023['overlap'] > 250]


    df_marker = pd.read_csv(f'{base_folder}/BICCN_enhancer_challenege/catlas_ccre/mouse/marker_all_info.csv')

    df_marker = df_marker.drop_duplicates('group')

    class_dict = dict(zip(df_marker.group, df_marker.classt))

    df_Zemke2023['group'] = [class_dict[x] if x in class_dict.keys() else 'del' for x in df_Zemke2023['cell_type'].tolist()]


    #df = df[df['subclass'].isin(['Glial & Endo', 'VLMC'])]
    #df = df[df['subclass'].isin(['CGE-derived', 'MGE-derived'])]
    #df = df[df['subclass'].isin(['IT-derived', 'Non-IT-derived'])]
    #df_Zemke2023 = df_Zemke2023[df_Zemke2023['cell_type'].isin(df['cell_type'].tolist())]
    #df_Zemke2023 = df_Zemke2023[df_Zemke2023['group']=='Glutamatergic']

    df_Zemke2023_table = df_Zemke2023.pivot_table(index='bin_id', columns='cell_type', values='rank', aggfunc='sum')

    df_Zemke2023_table.fillna(0, inplace=True)

    df_Zemke2023_table[df_Zemke2023_table != 0] = 1

    df_Zemke2023_human = df_Zemke2023_table.T
    #df_Zemke2023_human = df_Zemke2023_table[~df_Zemke2023_table.index.isin(['del'])]

    adata = ad.AnnData(df_Zemke2023_human)

    # Write AnnData object to a file

    #adata.obs_names = [f"gene_{i}" for i in gene_list]
    adata.var_names = [f"bin_{i}" for i in adata.var_names.tolist() ]

    z_scores = stats.zscore(adata.X, axis=0, nan_policy='omit')

    layer_name = f'z_scores_per_bin'

    adata.layers[layer_name] = z_scores

    adata.write_h5ad(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/zemke_brain.h5ad')  # Replace "your_output_file.h5ad" with your desired output file path





    df_heart = pd.read_csv(f'{base_folder}/BICCN_enhancer_challenege/catlas_ccre/human/hocker_heart/heart_table_s6.tsv', sep='\t', skiprows=1)
    df_heart.to_csv(f'{base_folder}/BICCN_enhancer_challenege/catlas_ccre/human/hocker_heart/heart.bed',header=False, index=False, sep='\t')

    os.system(f"~/.conda/envs/hicexplorer/bin/bedtools intersect -wo -a {base_folder}/BICCN_enhancer_challenege/catlas_ccre/human/hocker_heart/heart.bed -b {base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/regions_bed_file.tsv > {base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/cre_modules_heart.bed")
    df_hba_modules = pd.read_csv(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/cre_modules_heart.bed', sep='\t', names=['a', 'b','c' ,'logfc', 'p_val', 'cell_type', 'chr', 'start', 'end', 'bin_id', 'overlap'])


    #df_hba_modules = df_hba_modules[df_hba_modules['overlap'] > 250]

    df_hocker_table = df_hba_modules.pivot_table(index='bin_id', columns='cell_type', values='logfc', aggfunc='sum')

    df_hocker_table.fillna(0, inplace=True)

    df_hocker_table[df_hocker_table != 0] = 1

    df_hocker_human = df_hocker_table.T

    adata = ad.AnnData(df_hocker_human)

    # Write AnnData object to a file

    #adata.obs_names = [f"gene_{i}" for i in gene_list]
    adata.var_names = [f"bin_{i}" for i in adata.var_names.tolist() ]

    z_scores = stats.zscore(adata.X, axis=0, nan_policy='omit')

    layer_name = f'z_scores_per_bin'

    adata.layers[layer_name] = z_scores

    adata.write_h5ad(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/zemke_heart.h5ad')  # Replace "your_output_file.h5ad" with your desired output file path


    import pyBigWig



    name_category_dict = {
        'Astro-NT_NN': 'Astro',
        'Lamp5_Gaba': 'Lamp5',
        'Astro-TE_NN': 'Astro',
        'Lamp5_Lhx6_Gaba': 'Lamp5_Lhx6',
        'Endo_NN': 'Endo',
        'Microglia_NN': 'Micro-PVM',
        'L2_3_IT_CTX_Glut': 'L2/3 IT',
        'Oligo_NN': 'Oligo',
        'L4_5_IT_CTX_Glut': 'L4/5 IT',
        'OPC_NN': 'OPC',
        'L4_RSP-ACA_Glut': 'L4 RSP-ACA',
        'Peri_NN': 'Peri',
        'L5_ET_CTX_Glut': 'L5 ET',
        'Pvalb_chandelier_Gaba': 'Chandelier',
        'L5_IT_CTX_Glut': 'L5 IT',
        'Pvalb_Gaba': 'Pvalb',
        'L5_NP_CTX_Glut': 'L5 NP',
        'Sncg_Gaba': 'Sncg',
        'L6b_CTX_Glut': 'L6b',
        'Sst_Gaba': 'Sst',
        'L6_CT_CTX_Glut': 'L6 CT',
        'Vip_Gaba': 'Vip',
        'L6_IT_CTX_Glut': 'L6 IT',
        'VLMC_NN': 'VLMC'
    }

    species='mouse'
    SRP_name='aggregates'


    compartment_list  = []

    for f_name, f_mapped in zip(name_category_dict.keys(), name_category_dict.values()):

        f_path = "/grid/gillis/data_norepl/lohia/BICCN_enhancer_challenege/liu-2023-sn3c/compartment_score/"

        m_p = f"{f_path}/{f_name}.compartment_score.100K.bw"

        bw_file = pyBigWig.open(m_p)



        bedgraph_file = f'/grid/gillis/data_norepl/lohia/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/your_output_file.bedgraph'

        # Open the BedGraph file for writing
        with open(bedgraph_file, 'w') as f:
            for chrom in bw_file.chroms():
                # Iterate over each chromosome in the BigWig file
                intervals = bw_file.intervals(chrom)
                for interval in intervals:
                    # Write each interval to the BedGraph file
                    f.write(f"{chrom}\t{interval[0]}\t{interval[1]}\t{interval[2]}\n")


        # Close the BigWig file
        bw_file.close()

        os.system(f"~/.conda/envs/hicexplorer/bin/bedtools intersect -wo -b /grid/gillis/data_norepl/lohia/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/your_output_file.bedgraph -a /grid/gillis/data_norepl/lohia/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/regions_bed_file.tsv > {f_path}/intersect_{resolution}.bed")


        enhancer_bins = pd.read_csv(f'{f_path}/intersect_{resolution}.bed', sep='\t', names=['d', 'd1', 'd2', 'bin_id', 'c', 'c1', 'c2', 'compartment_score', 'overlap'])
        enhancer_bins['cell_type'] = f_mapped
        compartment_list.append(enhancer_bins)



    compartment_matrix = pd.concat(compartment_list)



    compartment_df = compartment_matrix.pivot_table(columns='bin_id', index='cell_type', values='compartment_score', aggfunc='mean')


    adata = ad.AnnData(compartment_df)

    # Write AnnData object to a file

    #adata.obs_names = [f"gene_{i}" for i in gene_list]
    adata.var_names = [f"bin_{i}" for i in adata.var_names.tolist() ]

    z_scores = stats.zscore(adata.X, axis=0, nan_policy='omit')

    layer_name = f'z_scores_per_bin'

    adata.layers[layer_name] = z_scores

    adata.write_h5ad(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/compartment.h5ad')  # Replace "your_output_file.h5ad" with your desired output file path
    
    


    




In [18]:
for resolution in [ '10kbp_raw']:
    get_atac_values(resolution)

<ipython-input-17-4fe53a83664f>:80: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['cell_type'] = keyl
<ipython-input-17-4fe53a83664f>:80: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['cell_type'] = keyl
<ipython-input-17-4fe53a83664f>:80: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning

Empty DataFrame
Columns: []
Index: []


ValueError: no types given

In [ ]:

no_of_markers_list = [1,2,3,4,5,6,7,8,9,10,11,12,13,15,17,19,21,23,25,29,33,37,41,46,50,58,65,73,82,92,100,115,129,144,150,162,181,200,227,250,284,300,356,400,446,500]     
for no_of_markers in no_of_markers_list:

    for species in ['mouse']:
        for process_type in ['intra']:
            for resolution in ['1kbp_raw']:
                for shuf in [False, True]:
                    for drop_duplicates in [False, True]:
                        for marker_name in ['brain_class']:
                            for dist in [1000]:
                                layer_name = 'z_scores'
                                base_folder = '/grid/gillis/data_norepl/lohia/'
                                SRP_name='aggregates'
                                ice_type='KR'
                                input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{process_type}_{dist}_{layer_name}_by_allbins_max.h5ad'
                                if species=='mouse':
                                    gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
                                else:
                                    gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 

                                input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean.h5ad'
                                input_file_another_exp_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/zemke_brain.h5ad'
                                outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean_atac.h5ad'
                                
                                if os.path.isfile(outputfile_h5ad):
                                    pass
                                else:
                                    calc_pair_corr(input_file_h5ad, input_file_another_exp_h5ad, outputfile_h5ad, marker_name)

                                input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean.h5ad'                            
                                input_file_another_exp_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/compartment.h5ad'
                                outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean_compartment.h5ad'
                                if os.path.isfile(outputfile_h5ad):
                                    pass
                                else:
                                    calc_pair_corr(input_file_h5ad, input_file_another_exp_h5ad, outputfile_h5ad, marker_name)





In [ ]:

no_of_markers_list = [1,2,3,4,5,6,7,8,9,10,11,12,13,15,17,19,21,23,25,29,33,37,41,46,50,58,65,73,82,92,100,115,129,144,150,162,181,200,227,250,284,300,356,400,446,500]     
for no_of_markers in no_of_markers_list:

    for species in ['human']:
        for process_type in ['intra']:
            for resolution in ['1kbp_raw']:
                for shuf in [False, True]:
                    for drop_duplicates in [False, True]:
                        for marker_name in ['brain_class']:
                            for dist in [1000]:
                                layer_name = 'z_scores'
                                base_folder = '/grid/gillis/data_norepl/lohia/'
                                SRP_name='aggregates'
                                ice_type='KR'
                                input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{process_type}_{dist}_{layer_name}_by_allbins_max.h5ad'
                                if species=='mouse':
                                    gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
                                else:
                                    gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 

                                input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean.h5ad'
                                input_file_another_exp_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/zemke_brain.h5ad'
                                outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean_atac.h5ad'
                                
                                if os.path.isfile(outputfile_h5ad):
                                    pass
                                else:
                                    calc_pair_corr(input_file_h5ad, input_file_another_exp_h5ad, outputfile_h5ad, marker_name)

                                input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean.h5ad'                            
                                input_file_another_exp_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/compartment.h5ad'
                                outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean_compartment.h5ad'




In [50]:

no_of_markers_list = [1,2,3,4,5,6,7,8,9,10,11,12,13,15,17,19,21,23,25,29,33,37,41,46,50,58,65,73,82,92,100,115,129,144,150,162,181,200,227,250,284,300,356,400,446,500]     
for no_of_markers in no_of_markers_list:

    for species in ['mouse']:
        for process_type in ['intra']:
            for resolution in ['1kbp_raw']:
                for shuf in [False, True]:
                    for drop_duplicates in [False, True]:
                        for marker_name in ['brain_class']:
                            for dist in [0]:
                                layer_name = 'z_scores'
                                base_folder = '/grid/gillis/data_norepl/lohia/'
                                SRP_name='aggregates'
                                ice_type='KR'
                                input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{process_type}_{dist}_{layer_name}_by_allbins_max.h5ad'
                                if species=='mouse':
                                    gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
                                else:
                                    gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 

                                input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean.h5ad'
                                input_file_another_exp_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/zemke_brain.h5ad'
                                outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean_atac.h5ad'
                                
                                #if os.path.isfile(outputfile_h5ad):
                                #    pass
                                #else:
                                calc_pair_corr(input_file_h5ad, input_file_another_exp_h5ad, outputfile_h5ad, marker_name)

                                input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean.h5ad'                            
                                input_file_another_exp_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/compartment.h5ad'
                                outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean_compartment.h5ad'
                                #if os.path.isfile(outputfile_h5ad):
                                #    pass
                                #else:
                                calc_pair_corr(input_file_h5ad, input_file_another_exp_h5ad, outputfile_h5ad, marker_name)





<ipython-input-49-75cd9e0004b4>:108: RuntimeWarning: invalid value encountered in true_divide
  auc_array = (((np.nansum(pos_rank_sum, axis=1) / (np.nansum(tp, axis=1))) - (np.nansum(tp, axis=1) + 1) / 2)) / np.nansum(tn, axis=1)


In [10]:
from hicmatrix import HiCMatrix as hm
from hicmatrix.lib import MatrixFileHandler
import numpy as np
import pandas as pd
from scipy import stats, sparse
import bottleneck
from scipy.stats import mannwhitneyu
import h5py
import os.path
import gc
import os
import matplotlib.pyplot as plt
from pyranges import read_gtf


from umap import UMAP
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
import scipy.spatial as sp, scipy.cluster.hierarchy as hc

import seaborn as sns


import anndata as ad
import scanpy as sc


#egad function

import numpy as np
import pandas as pd
from scipy import stats, sparse
import bottleneck


def run_egad(go, nw, **kwargs):
    """EGAD running function
    
    Wrapper to lower level functions for EGAD

    EGAD measures modularity of gene lists in co-expression networks. 

    This was translated from the MATLAB version, which does tiled Cross Validation
    
    The useful kwargs are:
    int - nFold : Number of CV folds to do, default is 3, 
    int - {min,max}_count : limits for number of terms in each gene list, these are exclusive values


    Arguments:
        go {pd.DataFrame} -- dataframe of genes x terms of values [0,1], where 1 is included in gene lists
        nw {pd.DataFrame} -- dataframe of co-expression network, genes x genes
        **kwargs 
    
    Returns:
        pd.DataFrame -- dataframe of terms x metrics where the metrics are 
        ['AUC', 'AVG_NODE_DEGREE', 'DEGREE_NULL_AUC', 'P_Value']
    """
    assert nw.shape[0] == nw.shape[1] , 'Network is not square'
    assert np.all(nw.index == nw.columns) , 'Network index and columns are not in the same order'
    nw_mask = nw.isna().sum(axis=1) != nw.shape[1]
    #print (nw_mask)
    nw = nw.loc[nw_mask, nw_mask].astype(float)
    #print (nw)
    #np.fill_diagonal(nw.values, 1)
    return _runNV(go, nw, **kwargs)


def _runNV(go, nw, nFold=3, min_count=1, max_count=1000):

    #Make sure genes are same in go and nw
    genes_intersect = go.index.intersection(nw.index)

    go = go.loc[genes_intersect, :]
    nw = nw.loc[genes_intersect, genes_intersect]

    #Make sure there aren't duplicates
    duplicates = nw.index.duplicated(keep='first')
    nw = nw.loc[~duplicates, ~duplicates]

    go = go.loc[:, (go.sum(axis=0) > min_count) & (go.sum(axis=0) < max_count)]
    go = go.loc[~go.index.duplicated(keep='first'), :]
    
    roc = _new_egad(go.values, nw.values, nFold)

    col_names = ['AUC', 'AVG_NODE_DEGREE', 'DEGREE_NULL_AUC', 'P_Value']
    #Put output in dataframe
    return pd.DataFrame(dict(zip(col_names, roc)), index=go.columns)


def _new_egad(go, nw, nFold):

    #Build Cross validated Positive
    x, y = np.where(go)
    cvgo = {}
    for i in np.arange(nFold):
        a = x[i::nFold]
        b = y[i::nFold]
        dat = np.ones_like(a)
        mask = sparse.coo_matrix((dat, (a, b)), shape=go.shape)
        cvgo[i] = go - mask.toarray()
        
    CVgo = np.concatenate(list(cvgo.values()), axis=1)

    sumin = np.matmul(nw.T, CVgo)

    degree = np.sum(nw, axis=0)

    predicts = sumin / degree[:, None]

    np.place(predicts, CVgo > 0, np.nan)
    


    #Calculate ranks of positives
    #rank_abs = lambda x: stats.rankdata(np.abs(x))
    #predicts2 = np.apply_along_axis(rank_abs, 0, predicts)
    predicts2  = bottleneck.nanrankdata(abs(predicts), axis=0)


    #Masking Nans that were ranked (how tiedrank works in matlab)
    predicts2[np.isnan(predicts)] = np.nan
    


    filtering = np.tile(go, nFold)

    #negatives :filtering == 0
    #Sets Ranks of negatives to 0
    np.place(predicts2, filtering == 0, 0)

    #Sum of ranks for each prediction
    p = bottleneck.nansum(predicts2, axis=0)

    #Number of predictions
    #Number of 1's masked for each GO term for each CV
    n_p = np.sum(filtering, axis=0) - np.sum(CVgo, axis=0)

    #Number of negatives
    #Number of GO terms - number of postiive
    n_n = filtering.shape[0] - np.sum(filtering, axis=0)

    roc = (p / n_p - (n_p + 1) / 2) / n_n
    U = roc * n_p * n_n
    Z = (np.abs(U - (n_p * n_n / 2))) / np.sqrt(n_p * n_n *
                                                (n_p + n_n + 1) / 12)
    roc = roc.reshape(nFold, go.shape[1])
    Z = Z.reshape(nFold, go.shape[1])
    #Stouffer Z method
    Z = bottleneck.nansum(Z, axis=0) / np.sqrt(nFold)
    #Calc ROC of Neighbor Voting
    roc = bottleneck.nanmean(roc, axis=0)
    P = stats.norm.sf(Z)

    #Average degree for nodes in each go term
    avg_degree = degree.dot(go) / np.sum(go, axis=0)

    #Calc null auc for degree
    ranks = np.tile(stats.rankdata(degree), (go.shape[1], 1)).T

    np.place(ranks, go == 0, 0)

    n_p = bottleneck.nansum(go, axis=0)
    nn = go.shape[0] - n_p
    p = bottleneck.nansum(ranks, axis=0)

    roc_null = (p / n_p - ((n_p + 1) / 2)) / nn

    return roc, avg_degree, roc_null, P


tissue_dict = {'Chandelier': "brain",
 'Lamp5': "brain",
 'Lamp5_Lhx6': "brain",
 'Pax6': "brain",
 'Pvalb': "brain",
 'Sncg': "brain",
 'Sst': "brain",
 'Chandelier': "brain",
 'Sst Chodl': "brain",
 'Meis2': "brain",
 'Vip': "brain",
 'L2/3 IT': "brain",
 'L4 IT': "brain",
 'L5 ET': "brain",
 'L5 IT': "brain",
 'L5 PT': "brain",
 'L4/5 IT': "brain",
 'L5/6 NP': "brain",
 'L6 CT': "brain",
 'L6 IT': "brain",
 'L6 IT Car3': "brain",
 'L6b': "brain",
 'Astro': 'brain',
 'Endo': 'brain',
 'Micro-PVM': 'brain',
 'OPC': 'brain',
 'Oligo': "brain",
 'VLMC':'brain', 
 'Peri': 'brain',
 'SMC': 'brain',
 'T cell': 'heart',
 'basophil': 'heart',
 'erythroblast': 'heart',
 'granulocyte': 'heart',
 'hematopoietic precursor cell': 'heart',
 'immature B cell': 'heart',
 'immature natural killer cell': 'heart',
 'late pro-B cell': 'heart',
 'macrophage': 'heart',
 'monocyte': 'heart',
 'naive B cell': 'heart',
 'pro-B cell': 'heart',
 'proerythroblast' : 'heart',
 'Adipocytes' : 'heart',
 'Cardiomyocytes': 'heart',
 'Endocardial': 'heart',
 'Endothelial_Arterial': 'heart' ,
 'Endothelial_Capillaries': 'heart',
 'Endothelial_Other': 'heart',
 'Endothelial_Venous': 'heart',
 'Fibroblasts': 'heart',
 'Pericytes_Stromal': 'heart',
 'Smooth_Muscle_Cells': 'heart',
 'Pericytes': 'heart',
 'Epicardium_FB-like': 'heart',
 'Epicardium_Meso': 'heart',
 'Epicardium_Proliferating': 'heart',
 'Immature_Cardiomyocytes': 'heart',
 'Immature_other': 'heart',
 'Lymphoid_Immune_Cells': 'heart',
 'Myeloid_Immune_Cells': 'heart',
 'Neuronal_Cells': 'heart',}


NvsNN_dict = {'Chandelier': "N",
 'Lamp5': "N",
 'Lamp5_Lhx6': "N",
 'Pax6': "N",
 'Pvalb': "N",
 'Sncg': "N",
 'Sst': "N",
 'Chandelier': "N",
 'Sst Chodl': "N",
 'Meis2': "N",
 'Vip': "N",
 'L2/3 IT': "N",
 'L4 IT': "N",
 'L5 ET': "N",
 'L5 IT': "N",
 'L5 PT': "N",
 'L4/5 IT': "N",
 'L5/6 NP': "N",
 'L6 CT': "N",
 'L6 IT': "N",
 'L6 IT Car3': "N",
 'L6b': "N",
 'Astro': 'NN',
 'Endo': 'NN',
 'Micro-PVM': 'NN',
 'OPC': 'NN',
 'Oligo': "NN",
 'VLMC':'NN', 
 'Peri': 'NN',
 'SMC': 'NN',
}

GlutvsGaba_dict = {'Chandelier': "Gaba",
 'Lamp5': "Gaba",
 'Lamp5_Lhx6': "Gaba",
 'Pax6': "Gaba",
 'Pvalb': "Gaba",
 'Sncg': "Gaba",
 'Sst': "Gaba",
 'Chandelier': "Gaba",
 'Sst Chodl': "Gaba",
 'Meis2': "Gaba",
 'Vip': "Gaba",
 'L2/3 IT': "Glut",
 'L4 IT': "Glut",
 'L5 ET': "Glut",
 'L5 IT': "Glut",
 'L5 PT': "Glut",
 'L4/5 IT': "Glut",
 'L5/6 NP': "Glut",
 'L6 CT': "Glut",
 'L6 IT': "Glut",
 'L6 IT Car3': "Glut",
 'L6b': "Glut",
 }

ITvsnIT_dict = {'L2/3 IT': "IT",
 'L4 IT': "IT",
 'L5 ET': "nIT",
 'L5 IT': "IT",
 'L5 PT': "nIT",
 'L4/5 IT': "IT",
 'L5/6 NP': "nIT",
 'L6 CT': "nIT",
 'L6 IT': "IT",
 'L6 IT Car3': "IT",
 'L6b': "nIT",
 }

def create_dict_from_columns(name_age_dict):
    # Create a dictionary from two columns of the DataFrame

    given_dict = name_age_dict.copy()
    
    n = len(given_dict.keys())
    tp_class = np.zeros((n, n))

    # Fill the diagonal elements with 1
    np.fill_diagonal(tp_class, 1)

    df_tp_class = pd.DataFrame(tp_class, index=given_dict.keys(), columns=given_dict.values())

    # Update the DataFrame based on the given_dict
    for key, value in given_dict.items():
        df_tp_class.loc[key, value] = 1

    # Remove duplicate columns
    df_tp_class = df_tp_class.loc[:, ~df_tp_class.columns.duplicated()]
    
    return df_tp_class

# Calculate the mean of genes for each category and observation, ignoring NaN values
def calculate_pearson_correlation(df_a, corr_method):
    # Calculate mean for each category (axis=0) and each observation (axis=1), ignoring NaN values


    df_corr = df_a.T.corr(min_periods=200, method=corr_method)
     
    return df_corr

# Call the function to calculate category means, ignoring NaN values



        

#for each marker-list and input file , I can make one output file

def calc_egad_vals(input_file_h5ad, outputfile_h5ad):

        

        adata = ad.read_h5ad(f'{input_file_h5ad}')
        
        np_of_col = len(adata.obs_names.tolist())
        np_of_rows = len(adata.obs_names.tolist())
        
        adata_l = ad.AnnData(np.zeros((np_of_rows, np_of_col)))
        
        layer_names = adata.layers.keys()    
        for corr_method in ['pearson']:
                        for given_layer in layer_names:



                                df_a = adata.to_df(layer=given_layer)

                                df_corr = calculate_pearson_correlation(df_a, corr_method)

                                l_n = f'{given_layer}_{corr_method}'

                                adata_l.layers[l_n] = df_corr

                                df_corr  = df_corr.fillna(0)
                                
                                df_corr += abs(df_corr.min().min())
                                
                                #print (df_corr)

                                #df_list  = []
                                
                                if marker_name == 'brain_class':
                                    name_age_dict =  NvsNN_dict.copy()
                                    class_name = ['NvsNN']
                                elif marker_name == 'Glutamatergic':
                                    name_age_dict =  ITvsnIT_dict.copy()
                                    class_name = ['ITvsnIT']
                                    
                                else:
                                    name_age_dict =  tissue_dict.copy()
                                    class_name = 'tissue'
                                    
                                    

                                #for name_age_dict, class_name in zip([tissue_dict , NvsNN_dict], ['tissue' , 'NvsNN']):

                                df_tp_class = create_dict_from_columns(name_age_dict)

                                df_exp = run_egad(df_tp_class, df_corr)

                                #    df_list.append(df_exp)
                                #df_exp = pd.concat(df_list)

                                adata_l.uns[l_n] = df_exp



        adata_l.obs_names = adata.obs_names.tolist()
        adata_l.var_names = adata.obs_names.tolist()

        adata_l.write(outputfile_h5ad, compression="gzip")



In [11]:
no_of_markers_list = [1,2,3,4,5,6,7,8,9,10,11,12,13,15,17,19,21,23,25,29,33,37,41,46,50,58,65,73,82,92,100,115,129,144,150,162,181,200,227,250,284,300,356,400,446,500]     
for no_of_markers in no_of_markers_list:

    for species in ['mouse', 'human']:
        for process_type in ['inter']:
            for resolution in ['10kbp_raw']:
                for shuf in [True, False]:
                    for drop_duplicates in [True, False]:
                        for marker_name in ['Glutamatergic']:
                            dist = 0
                            layer_name = 'z_scores'
                            base_folder = '/grid/gillis/data_norepl/lohia/'
                            SRP_name='aggregates'
                            ice_type='KR'
                            if species=='mouse':
                                gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
                            else:
                                gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 
                            input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean.h5ad'
                            outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean_egad.h5ad'
                            if os.path.isfile(outputfile_h5ad):
                                    pass
                            else:
                                    calc_egad_vals(input_file_h5ad, outputfile_h5ad)
                            


<ipython-input-10-d318a7bff28f>:143: RuntimeWarning: invalid value encountered in true_divide
  roc = (p / n_p - (n_p + 1) / 2) / n_n
<ipython-input-10-d318a7bff28f>:143: RuntimeWarning: invalid value encountered in true_divide
  roc = (p / n_p - (n_p + 1) / 2) / n_n
<ipython-input-10-d318a7bff28f>:143: RuntimeWarning: invalid value encountered in true_divide
  roc = (p / n_p - (n_p + 1) / 2) / n_n
<ipython-input-10-d318a7bff28f>:143: RuntimeWarning: invalid value encountered in true_divide
  roc = (p / n_p - (n_p + 1) / 2) / n_n
<ipython-input-10-d318a7bff28f>:143: RuntimeWarning: invalid value encountered in true_divide
  roc = (p / n_p - (n_p + 1) / 2) / n_n
<ipython-input-10-d318a7bff28f>:143: RuntimeWarning: invalid value encountered in true_divide
  roc = (p / n_p - (n_p + 1) / 2) / n_n
<ipython-input-10-d318a7bff28f>:143: RuntimeWarning: invalid value encountered in true_divide
  roc = (p / n_p - (n_p + 1) / 2) / n_n
<ipython-input-10-d318a7bff28f>:143: RuntimeWarning: invalid v

In [58]:


no_of_markers_list = [1,2,3,4,5,6,7,8,9,10,11,12,13,15,17,19,21,23,25,29,33,37,41,46,50,58,65,73,82,92,100,115,129,144,150,162,181,200,227,250,284,300,356,400,446,500]     
for no_of_markers in no_of_markers_list:

    for species in ['mouse']:
        for process_type in ['intra', 'inter']:
            for resolution in [ '250kbp_raw', '100kbp_raw', '40kbp_raw', '10kbp_raw']:
                for shuf in [True, False]:
                    for drop_duplicates in [True, False]:
                        for marker_name in ['brain_class', 'brain_blood']:
                            dist = 0
                            layer_name = 'z_scores'
                            base_folder = '/grid/gillis/data_norepl/lohia/'
                            SRP_name='aggregates'
                            ice_type='KR'
                            if species=='mouse':
                                gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
                            else:
                                gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 
                            input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean.h5ad'
                            outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean_egad.h5ad'
                            if os.path.isfile(outputfile_h5ad):
                                    pass
                            else:
                                    calc_egad_vals(input_file_h5ad, outputfile_h5ad)
                            

no_of_markers_list = [1,2,3,4,5,6,7,8,9,10,11,12,13,15,17,19,21,23,25,29,33,37,41,46,50,58,65,73,82,92,100,115,129,144,150,162,181,200,227,250,284,300,356,400,446,500]     
for no_of_markers in no_of_markers_list:
    for species in ['human']:
        for process_type in ['intra', 'inter']:
            for resolution in [ '250kbp_raw', '100kbp_raw', '40kbp_raw', '10kbp_raw']:
                for shuf in [True, False]:
                    for drop_duplicates in [True, False]:
                        for marker_name in ['brain_class', 'brain_heart']:
                            dist = 0
                            layer_name = 'z_scores'
                            base_folder = '/grid/gillis/data_norepl/lohia/'
                            SRP_name='aggregates'
                            ice_type='KR'
                            if species=='mouse':
                                gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
                            else:
                                gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 
                            input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean.h5ad'
                            outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean_egad.h5ad'
                            if os.path.isfile(outputfile_h5ad):
                                    pass
                            else:
                                    calc_egad_vals(input_file_h5ad, outputfile_h5ad)
